In [1]:
import os
from dotenv import load_dotenv
import pandas as pd
import psycopg2
from math import radians, cos, sin, asin, sqrt
import plotly.graph_objects as go
import plotly.express as p

pd.set_option('display.max_columns', 100)
load_dotenv()

True

In [3]:
df = pd.read_csv('GeoObjectsV2_3Mar2020.csv', encoding = "ISO-8859-1")

In [4]:
df.head()

Obj_ID  Obj_ParentID  Obj_CountryID  Obj_TypeID Obj_Code  Obj_Code2  \
0       1             0              0           1      NaN        NaN   
1       2             0              0           1      NaN        NaN   
2       3             0              0           1      NaN        NaN   
3       4             0              0           1      NaN        NaN   
4       5             0              0           1      NaN        NaN   

  Obj_StateCode Obj_AirportCodes     Obj_Name Obj_Keywords  Obj_GIATA  \
0           NaN              NaN       Africa          NaN        NaN   
1           NaN              NaN         Asia          NaN        NaN   
2           NaN              NaN  Australasia          NaN        NaN   
3           NaN              NaN       Europe          NaN        NaN   
4           NaN              NaN  Middle East          NaN        NaN   

   Obj_FBLocationID  Obj_Priority  Obj_StopParent  Obj_IsDeleted  \
0               NaN             0               0              0   
1               NaN             0               0              0   
2               NaN             0               0              0   
3               NaN             0               0              0   
4               NaN             0               0              0   

  Obj_UpdatedDateTime Obj_CreatedDateTime Obj_SourceRef Obj_Description  \
0    2009-03-09 22:58    2009-03-09 22:58           NaN             NaN   
1    2009-03-09 22:58    2009-03-09 22:58           NaN             NaN   
2    2009-03-09 22:58    2009-03-09 22:58           NaN             NaN   
3    2009-03-09 22:58    2009-03-09 22:58           NaN             NaN   
4    2009-03-09 22:58    2009-03-09 22:58           NaN             NaN   

   Obj_WeatherCode Obj_CurrencyCode  Obj_Lon  Obj_Lat Obj_Geo  Obj_MapZoom  \
0              NaN              NaN      NaN      NaN     NaN          NaN   
1              NaN              NaN      NaN      NaN     NaN          NaN   
2              NaN              NaN      NaN      NaN     NaN          NaN   
3              NaN              NaN      NaN      NaN     NaN          NaN   
4              NaN              NaN      NaN      NaN     NaN          NaN   

  Obj_Alternatives Obj_Path  Obj_IsHidden  Obj_NamePath  \
0              NaN      /1/             0       /Africa   
1              NaN      /2/             0         /Asia   
2              NaN      /3/             0  /Australasia   
3              NaN      /4/             0       /Europe   
4              NaN      /5/             0  /Middle East   

   Obj_AllowOnCombinedDP  Obj_AllowOnNonPH  Obj_GlobalHidden  Obj_Active  
0                      1                 1                 0           1  
1                      1                 1                 0           1  
2                      1                 1                 0           1  
3                      1                 1                 0           1  
4                      1                 1                 0           1

In [5]:
df = df.dropna(axis=0, subset=['Obj_AirportCodes', 'Obj_Name', 'Obj_Lon', 'Obj_Lat'], how='any')

In [6]:
df.sample(5)

Obj_ID  Obj_ParentID  Obj_CountryID  Obj_TypeID Obj_Code  Obj_Code2  \
133939  142064          1473             17           6      JUJ        NaN   
105450  113512           177             25          10      BGI        NaN   
5951      8256            89             89           5      MSU        NaN   
50098    56245          1047             20           5      ADL        NaN   
77093    85155          1093            158          10      LAX        NaN   

       Obj_StateCode Obj_AirportCodes                       Obj_Name  \
133939           NaN              JUJ  Libertador General San Martín   
105450           NaN              BGI       Harry Bayley Observatory   
5951             NaN              MSU                         Maseru   
50098            NaN              ADL                       Ovingham   
77093            NaN              LAX             El Capitan Theatre   

       Obj_Keywords  Obj_GIATA  Obj_FBLocationID  Obj_Priority  \
133939          NaN        NaN               NaN             0   
105450          NaN        NaN               NaN             0   
5951            NaN        NaN               NaN             0   
50098           NaN        NaN               NaN             0   
77093           NaN        NaN               NaN             0   

        Obj_StopParent  Obj_IsDeleted Obj_UpdatedDateTime Obj_CreatedDateTime  \
133939               0              0    2019-04-30 14:48    2019-04-30 14:48   
105450               0              0    2016-02-29 18:42    2016-02-29 15:32   
5951                 0              0    2009-03-27 16:12    2009-03-27 16:12   
50098                1              0    2013-06-18 18:06    2013-06-18 18:06   
77093                0              0    2016-02-29 18:13    2016-02-29 14:55   

       Obj_SourceRef Obj_Description  Obj_WeatherCode Obj_CurrencyCode  \
133939           NaN             NaN              NaN              NaN   
105450       6061264             NaN              NaN              NaN   
5951             NaN             NaN              NaN              NaN   
50098            NaN             NaN              NaN              NaN   
77093        6159836             NaN              NaN              NaN   

           Obj_Lon    Obj_Lat                                         Obj_Geo  \
133939  -64.792826 -23.815332  0xE6100000010CC66D3480B7D037C03411363CBD3250C0   
105450  -59.584286  13.088131  0xE6100000010C228E75711B2D2A40C286A757CACA4DC0   
5951     27.483333 -29.316667  0xE6100000010CA9A44E4013513DC024287E8CB97B3B40   
50098   138.584349 -34.895911  0xE6100000010C423EE8D9AC7241C0A69BC420B0526140   
77093  -118.339859  34.101549  0xE6100000010CA245B6F3FD0C4140F6285C8FC2955DC0   

        Obj_MapZoom Obj_Alternatives                             Obj_Path  \
133939          NaN              NaN                                  NaN   
105450          NaN              NaN        /113512/177/17489/18571/25/7/   
5951            NaN              NaN                          /8256/89/1/   
50098           NaN              NaN                    /56245/1047/20/3/   
77093           NaN              NaN  /85155/1093/17972/18232/1000/158/6/   

        Obj_IsHidden            Obj_NamePath  Obj_AllowOnCombinedDP  \
133939             0                     NaN                      1   
105450             0                     NaN                      1   
5951               0  /Maseru/Lesotho/Africa                      1   
50098              0                     NaN                      1   
77093              0                     NaN                      1   

        Obj_AllowOnNonPH  Obj_GlobalHidden  Obj_Active  
133939                 1                 0           1  
105450                 1                 0           1  
5951                   1                 0           1  
50098                  1                 0           1  
77093                  1                 0           1

In [7]:
df['Obj_Name'].value_counts()

Plaza de Armas                21
Central Park                  19
Olympic Stadium               16
Museum of Contemporary Art    16
National Museum               16
                              ..
Hostos Park                    1
Saint Mary                     1
Luabo                          1
Barcelona Egyptian Museum      1
Nash Farm                      1
Name: Obj_Name, Length: 84479, dtype: int64

There are many common names.

In [8]:
df.loc[df['Obj_Name'] == 'Central Park'][['Obj_AirportCodes', 'Obj_Name', 'Obj_Lon', 'Obj_Lat']]

Obj_AirportCodes      Obj_Name     Obj_Lon    Obj_Lat
11123               JFK  Central Park  -73.965355  40.782865
52009           MEL,HLT  Central Park  133.775136 -25.274398
70194               NYC  Central Park  -73.965028  40.783700
70324               NBO  Central Park   36.817137  -1.286460
71278               YVR  Central Park -123.020956  49.222019
91984               KHH  Central Park  120.298098  22.623900
101706              CJS  Central Park -106.426803  31.684987
105012          HOU,IAH  Central Park -100.963334  35.540597
108639              CGK  Central Park  106.790907  -6.176385
109291              AHN  Central Park  -95.855262  32.194472
110865              YYC  Central Park -115.572894  51.174278
114154              SAP  Central Park  -88.025257  15.505477
117430      SJC,OAK,SFO  Central Park -121.977527  37.339995
122450              SJO  Central Park  -84.079582   9.933203
125496      XHH,WHH,WBU  Central Park -105.278505  40.015128
126630      FEG,AZN,NMA  Central Park   71.779774  40.386836
126793              BRK  Central Park  145.925790 -30.096991
128626              SJO  Central Park  -84.213870  10.016498
129404      SLC,PVU,OGD  Central Park  -88.310274  36.619265

In [9]:
df['Obj_Active'].value_counts()

1    90045
0       18
Name: Obj_Active, dtype: int64

Don't know why there are inactive Obj, but not many, self-decided to include them in the analysis.

Use airport data and seat capacity data, then keep the airports we are interest.

In [10]:
query = """
    SELECT "code", "lat", "lng", "name", "country_name"
    FROM airport_locations
    where lat is not null
"""
db_url = f'postgresql://{os.environ["PG_USER"]}:{os.environ["PG_PASSWORD"]}@{os.environ["PG_HOST"]}/dataportal'
airports_df = pd.read_sql_query(query, db_url)

In [11]:
# EC's code
query = """
    SELECT "Dest", "Airline Type", SUM("Seats") as "Annual Seats"
    FROM capacity
    GROUP BY "Dest", "Airline Type"
    ORDER BY "Dest"
"""
db_url = f'postgresql://{os.environ["PG_USER"]}:{os.environ["PG_PASSWORD"]}@{os.environ["PG_HOST"]}/dataportal'
seats_df = pd.read_sql_query(query, db_url)
# only include the airline types we care about
# aggregate by Dest IATA
seats_df = (
    seats_df
    .loc[seats_df['Airline Type'].isin(['Scheduled Passenger', 'Scheduled Passenger/Cargo'])]
    .groupby(['Dest'])
    .sum()
)

# Only keep the airports we care about
airports_df = airports_df[airports_df.code.isin(seats_df.index)]

In [12]:
airports_df.head()

code        lat         lng                             name  \
0   AAA -17.355101 -145.508499                             Anaa   
4   AAE  36.822201    7.809400                      Rabah Bitat   
11  AAL  57.093102    9.850000                          Aalborg   
13  AAN  24.261700   55.609200             Al Ain International   
15  AAP  -0.371900  117.257202  Aji Pangeran Tumenggung Airport   

            country_name  
0       French Polynesia  
4                Algeria  
11               Denmark  
13  United Arab Emirates  
15             Indonesia

In [13]:
df = df[['Obj_AirportCodes', 'Obj_Name', 'Obj_Lon', 'Obj_Lat']]

In [14]:
# Separate rows
# https://stackoverflow.com/questions/12680754/split-explode-pandas-dataframe-string-entry-to-separate-rows

def explode(df, lst_cols, fill_value='', preserve_index=False):
    # make sure `lst_cols` is list-alike
    if (lst_cols is not None
        and len(lst_cols) > 0
        and not isinstance(lst_cols, (list, tuple, np.ndarray, pd.Series))):
        lst_cols = [lst_cols]
    # all columns except `lst_cols`
    idx_cols = df.columns.difference(lst_cols)
    # calculate lengths of lists
    lens = df[lst_cols[0]].str.len()
    # preserve original index values    
    idx = np.repeat(df.index.values, lens)
    # create "exploded" DF
    res = (pd.DataFrame({
                col:np.repeat(df[col].values, lens)
                for col in idx_cols},
                index=idx)
             .assign(**{col:np.concatenate(df.loc[lens>0, col].values)
                            for col in lst_cols}))
    # append those rows that have empty lists
    if (lens == 0).any():
        # at least one list in cells is empty
        res = (res.append(df.loc[lens==0, idx_cols], sort=False)
                  .fillna(fill_value))
    # revert the original index order
    res = res.sort_index()
    # reset index if requested
    if not preserve_index:        
        res = res.reset_index(drop=True)
    return res

In [15]:
df = explode(df.assign(Obj_AirportCodes=df.Obj_AirportCodes.str.split(',')), 'Obj_AirportCodes')

In [16]:
df.tail()

Obj_Lat   Obj_Lon      Obj_Name Obj_AirportCodes
133469  48.469811  7.726144     Plobsheim              SXB
133470  48.658010  7.827133  La Wantzenau              BSL
133471  48.658010  7.827133  La Wantzenau              SXB
133472  48.829742  7.963965  Soufflenheim              BSL
133473  48.829742  7.963965  Soufflenheim              SXB

In [17]:
# merge POI df with airports df

result = pd.merge(df, airports_df, how='inner', left_on='Obj_AirportCodes', right_on='code').drop('code', axis=1)

In [18]:
result.sample(5)

Obj_Lat     Obj_Lon                              Obj_Name  \
11907  45.430255   12.325808                 Squero di San Trovaso   
41034  53.798900   -1.542070             City Varieties Music Hall   
9813   28.665344   77.230282                      St. James Church   
87095  51.454568    7.012340                        Grillo-Theater   
46821  45.462840 -122.656984  Ping Pong's Pint Sized Puppet Museum   

      Obj_AirportCodes        lat        lng                  name  \
11907              TSF  45.683300  12.083300        Venice-Treviso   
41034              LPL  53.338299  -2.866700   John Lennon Airport   
9813               AGR  27.158300  77.962799          Agra Airport   
87095              DTM  51.516701   7.466700      Dortmund Airport   
46821              PWM  43.644402 -70.303596  Portland Intl Jetprt   

         country_name  
11907           Italy  
41034  United Kingdom  
9813            India  
87095         Germany  
46821   United States

In [19]:
# get the distance between 2 GPS points
# Source: https://stackoverflow.com/questions/4913349/haversine-formula-in-python-bearing-and-distance-between-two-gps-points

def distance(lon1, lat1, lon2, lat2):
    """
    Calculate the great circle distance between two points
    on the earth (specified in decimal degrees)

    All args must be of equal length.    

    """
    lon1, lat1, lon2, lat2 = map(np.radians, [lon1, lat1, lon2, lat2])

    dlon = lon2 - lon1
    dlat = lat2 - lat1

    a = np.sin(dlat/2.0)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon/2.0)**2

    c = 2 * np.arcsin(np.sqrt(a))
    km = 6371 * c  # 6371 is Radius of earth in kilometers. Use 3956 for miles
    return km

In [20]:
result['distance_km'] = distance(result['Obj_Lat'], result['Obj_Lon'], result['lat'], result['lng'])

In [21]:
result.loc[result['Obj_Name'] == "Santa Fe Children's Museum"]

Obj_Lat     Obj_Lon                    Obj_Name Obj_AirportCodes  \
49893  35.673369 -105.936517  Santa Fe Children's Museum              ABQ   
49926  35.673369 -105.936517  Santa Fe Children's Museum              YES   

             lat         lng                   name   country_name  \
49893  35.041698 -106.606399  International Sunport  United States   
49926  30.683300   51.545200         Yasouj Airport           Iran   

        distance_km  
49893     77.042414  
49926  17500.423426

In [22]:
result.loc[result['Obj_Name'] == "Stillwater"]

Obj_Lat    Obj_Lon    Obj_Name Obj_AirportCodes        lat        lng  \
55507  42.93841 -73.653173  Stillwater              OKC  35.393101 -97.600601   
55666  42.93841 -73.653173  Stillwater              TUL  36.197800 -95.889702   

                      name   country_name  distance_km  
55507    Will Rogers World  United States  2657.768623  
55666  Tulsa International  United States  2469.226142

In [23]:
result.loc[result['Obj_Name'] == "CN Tower"]

Obj_Lat     Obj_Lon  Obj_Name Obj_AirportCodes        lat     lng  \
55723  56.130366 -106.346771  CN Tower              YYZ  43.679699 -79.625   
55746  43.642566  -79.387679  CN Tower              YYZ  43.679699 -79.625   

                                 name country_name  distance_km  
55723  Toronto Lester B. Pearson Intl       Canada  2954.391168  
55746  Toronto Lester B. Pearson Intl       Canada    26.399602

In [24]:
result.loc[result['Obj_Name'] == "Grand Central Station"]

Obj_Lat     Obj_Lon               Obj_Name Obj_AirportCodes  \
53663  34.16184 -118.283932  Grand Central Station              JFK   

             lat        lng                 name   country_name  distance_km  
53663  40.638599 -73.776901  John F Kennedy Intl  United States  4941.272435

In [25]:
result.loc[(result['country_name'] == 'United States') & (result['distance_km'] <= 300)].sort_values(by=['distance_km'], ascending=False).head(50)

Obj_Lat     Obj_Lon                                      Obj_Name  \
69947   37.034861  -78.897986      Red Hill Patrick Henry National Memorial   
35578   37.715459 -119.677077                                   Tunnel View   
64677   38.348371  -89.375818                       Nashville Memorial Park   
54938   36.420747  -81.470609                 Museum of Ashe County History   
54939   36.434680  -81.468539                               Ash County Park   
107894  40.664733  -74.387481   Bowcraft Amusement Park (Bowcraft Playland)   
35021   36.313435 -119.772944                                 Heritage Park   
35272   34.600450 -120.193083                                  Mosby Winery   
35430   37.213358 -119.699434  Picayune Rancheria of the Chukchansi Indians   
43213   30.520634  -83.991277                             Letchworth Mounds   
35020   36.283748 -119.784280                           Lemoore Golf Course   
35190   36.767834 -119.731764                              Discovery Center   
42769   41.610666  -79.741390                                    Titusville   
65635   30.102013  -98.012778                         Duchman Family Winery   
46554   46.519392  -67.835537                             Big Rock Ski Area   
35429   37.212603 -119.708928                    Coarsegold Historic Museum   
35022   36.301141 -119.789131               Sarah A. Mooney Memorial Museum   
106911  37.306268 -107.347135                      Piedra River Hot Springs   
45712   45.318120  -85.243216                    Lake Chalevoix Depot Beach   
69955   36.708729  -78.869270                         South Boston Speedway   
34171   36.809027 -119.737694                              Save Mart Center   
104577  36.883843  -81.526789                      Hungry Mother State Park   
66345   33.684058 -112.082941                                   Deer Valley   
66340   33.684058 -112.082941                                   Deer Valley   
108066  42.307336  -79.606918                         Johnson Estate Winery   
35191   36.731541 -119.751224                            Fresno Fairgrounds   
66311   26.194376  -97.910551                           Palms at Mid Valley   
34172   36.814980 -119.745033          California State University - Fresno   
104578  36.833268  -81.518946                               Lincoln Theatre   
35193   36.964458 -119.738983                                Lost Lake Park   
107134  41.464535  -96.915570                                        Rogers   
45562   45.320950  -85.259439                              Charlevoix Beach   
46119   43.194027  -96.304581                         Rock Valley Golf Club   
55509   35.914335  -94.949914                       Tahlequah City Hospital   
69936   38.015048  -78.840900                   Veritas Vineyard and Winery   
66255   32.706110  -97.906222                         Canyon West Golf Club   
43717   34.235639  -83.869476                  Gainesville Theatre Alliance   
35196   36.813258 -119.756449                                  Beiden Field   
43719   34.228756  -83.868214                College Square Shopping Center   
65479   30.347980  -97.987340                            Hills Country Club   
35195   36.813198 -119.758069                               Bulldog Stadium   
106910  37.353106 -107.323947                            Piedra River Trail   
35580   37.686098 -119.730952              Yosemite Arch Rock Gate Entrance   
104224  38.912207  -97.212315                             Eisenhower Center   
69942   38.258528  -78.827036                                 Grand Caverns   
104225  38.912397  -97.213928                        Greyhound Hall of Fame   
46120   43.210822  -96.292930                Winterfield Boat and Fish Area   
65946   26.159481  -97.889300             Rio Grande Valley Premium Outlets   
55334   34.218125  -84.346427                               Tanglewood Farm   
106551  39.401526 -107.341520                      Sunlight 

In [70]:
result.loc[result['country_name'] == 'Canada'].sort_values(by=['distance_km'], ascending=False).head(50)

Obj_Lat     Obj_Lon                                   Obj_Name  \
53632 -25.274398  133.775136                           Sydney surrounds   
75635 -33.445061  149.554473                      Mount Panorama Winery   
75636 -33.439235  149.561857               National Motor Racing Museum   
75632 -33.417653  149.581031                                   Bathurst   
75634 -33.418171  149.586898        Bathurst Visitor Information Centre   
33904   0.000000    0.000000              Save on Foods Memorial Centre   
34002   0.000000    0.000000              Save on Foods Memorial Centre   
80689   0.000000    0.000000                  Bell MTS Place (Manitoba)   
56613 -76.016094  -30.234375                                  Tremblant   
55427  60.516009 -150.701988                              Bings Landing   
79729  45.245556  -66.090420                                  Doc Creek   
79736  45.245556  -66.090420                                  Doc Creek   
80984  45.662881  -75.346156                                       Mayo   
33837  46.214970  -63.491170                         Victoria Playhouse   
33973  46.214970  -63.491170                         Victoria Playhouse   
80284  49.102842 -118.677686                           Greenwood Museum   
79245  45.783333  -75.316667                              Knights Inlet   
79268  45.783333  -75.316667                              Knights Inlet   
79768  45.783333  -75.316667                              Knights Inlet   
79860  56.130366 -106.346771                            Daniels Harbour   
80248  56.130366 -106.346771                            Daniels Harbour   
81075  56.130366 -106.346771                                     Saglek   
33639  42.870723  -79.355188                                    Burnaby   
33647  43.647935  -79.381752                         Financial District   
56621  51.268700 -117.509167                      Glacier National Park   
57223  51.283040 -117.074430              Stairway to Heaven Chair Lift   
57222  51.298110 -117.054860                         Pioneer Chair Lift   
56950  51.299077 -117.052454              Kicking Horse Mountain Resort   
57221  51.297740 -117.048380                       Golden Eagle Express   
57220  51.297280 -117.047920                       Catamount Chair Lift   
57227  51.408800 -117.043170   Burges and James Gadsden Provincial Park   
57219  51.412520 -117.009800       Northern Lights Wildlife Wolf Center   
57218  51.332800 -117.007710                           Golden Golf Club   
57228  51.318700 -116.971980                          Edelweiss Village   
57226  51.299660 -116.968370            Kicking Horse Pedestrian Bridge   
57230  51.296520 -116.966700       Golden and District General Hospital   
57225  51.292190 -116.961450                 Golden and District Museum   
57229  51.296172 -116.955555       College of the Rockies Golden Campus   
57109  51.301920 -116.954290  British Columbia Visitor Centre at Golden   
57231  51.296194 -116.953213      Golden and District Recreation Centre   
56622  51.403868 -116.482024                         Yoho National Park   
80381  56.304670 -112.232341                                 Lagrande 4   
80752  56.130366 -106.346771                                     Saglek   
80073  45.984348  -73.446481                                    St Paul   
55733  50.302757 -119.213956                                Silver Star   
80888  56.130366 -106.346771                         Maricourt Airstrip   
80889  56.130366 -106.346771                                     Saglek   
80252  49.166706  -57.431632                                  Deer Lake   
79532  56.130366 -106.346771                         Maricourt Airstrip   
79900  45.984348  -73.446481                                    St Paul   

      Obj_AirportCodes        lat         lng                            name  \
53632              YQY  46.166698  -60.049999            J.A. Douglas McCurdy   
75635              ZB

The worst were all seem to be completely wrong airports.

In [26]:
result.loc[result['Obj_Name'] == 'Central Park']

Obj_Lat     Obj_Lon      Obj_Name Obj_AirportCodes        lat  \
10265   -6.176385  106.790907  Central Park              CGK  -6.125800   
14330   -1.286460   36.817137  Central Park              NBO  -1.316700   
33230   51.174278 -115.572894  Central Park              YYC  51.112801   
33675   49.222019 -123.020956  Central Park              YVR  49.187199   
35202   37.339995 -121.977527  Central Park              SFO  37.619400   
35775   37.339995 -121.977527  Central Park              OAK  37.723598   
53672   40.782865  -73.965355  Central Park              JFK  40.638599   
65323   35.540597 -100.963334  Central Park              IAH  29.983299   
66034   35.540597 -100.963334  Central Park              HOU  29.645000   
66563   36.619265  -88.310274  Central Park              SLC  40.784199   
68447  -25.274398  133.775136  Central Park              MEL -37.661701   
76312   15.505477  -88.025257  Central Park              SAP  15.451400   
84271    9.933203  -84.079582  Central Park              SJO   9.993900   
84302   10.016498  -84.213870  Central Park              SJO   9.993900   
92523   40.386836   71.779774  Central Park              NMA  40.983299   
92676   40.386836   71.779774  Central Park              FEG  40.350300   
94491   31.684987 -106.426803  Central Park              CJS  31.637199   
99894   22.623900  120.298098  Central Park              KHH  22.572500   
105910  37.339995 -121.977527  Central Park              SJC  37.361099   
110830  36.619265  -88.310274  Central Park              OGD  41.196400   
110876  36.619265  -88.310274  Central Park              PVU  40.218102   

               lng                          name   country_name  distance_km  
10265   106.657799           Soekarno-Hatta Intl      Indonesia    14.889199  
14330    36.930801            Jomo Kenyatta Intl          Kenya    12.921971  
33230  -114.019699                  Calgary Intl         Canada   172.731165  
33675  -123.185303                Vancouver Intl         Canada    18.396455  
35202  -122.372803            San Francisco Intl  United States    46.963150  
35775  -122.215599            Metro Oakland Intl  United States    34.849115  
53672   -73.776901           John F Kennedy Intl  United States    21.423700  
65323   -95.339996  George Bush Intercontinental  United States   630.672302  
66034   -95.278603               William P Hobby  United States   638.037832  
66563  -111.966904           Salt Lake City Intl  United States  2630.034655  
68447   144.833298             Melbourne Airport      Australia  1609.293395  
76312   -87.924202         Ramon V. Morales Intl       Honduras    11.238815  
84271   -84.208900          Juan Santamaria Intl     Costa Rica    14.396031  
84302   -84.208900          Juan Santamaria Intl     Costa Rica     0.607933  
92523    71.599998                      Namangan     Uzbekistan    28.874573  
92676    71.733597         Fergana International     Uzbekistan     5.289836  
94491  -106.428596         Abraham Gonzalez Intl         Mexico     1.515928  
99894   120.345299                Kaohsiung Intl         Taiwan     5.989359  
105910 -121.925598            San Jose Municipal  United States     5.906266  
110830 -112.010803               Ogden Municipal  United States  2634.819927  
110876 -111.722199               Provo Municipal  United States  2602.942133

3 Central Parks share the same location but different airports and none of them makes sense. 

In [27]:
us = result.loc[result['country_name'] == 'United States']
fig = px.histogram(us, x="distance_km")
fig.show()

In [28]:
fig = go.Figure(data=[go.Histogram(x=us['distance_km'], histnorm='probability')])
fig.update_layout(title_text='POI and airport pairs distance probability distribution in US')
fig.show()

In [29]:
us.loc[us['distance_km'] == 0]

Obj_Lat  Obj_Lon              Obj_Name Obj_AirportCodes        lat  \
112804  33.450298 -88.5914  Golden Triangle Reg.              GTR  33.450298   

            lng                  name   country_name  distance_km  
112804 -88.5914  Golden Triangle Regl  United States          0.0

In [30]:
us['distance_km'].describe()

count    27070.000000
mean       554.259701
std       1364.121451
min          0.000000
25%         12.622079
50%         41.092234
75%        240.135501
max      17856.248228
Name: distance_km, dtype: float64

In [31]:
us.loc[us['distance_km'] <= 250].sort_values(by=['distance_km'], ascending=False).head(50)

Obj_Lat     Obj_Lon                           Obj_Name  \
45482   44.682004  -85.662344                       Wuerfel Park   
92165   13.444167  142.546309                               Guam   
45782   43.039285  -85.659907               Fifth Third Ballpark   
49144   35.352481  -96.935721             Shawnee Little Theatre   
109361  39.823490  -89.012810     Rock Springs Conservation Area   
65949   30.954726  -97.515599               Mill Creek Golf Club   
34529   40.365839 -120.651074         Diamond Mountain Golf Club   
66086   26.072322  -97.485419                   Little Graceland   
65478   30.505310  -97.579180               Star Ranch Golf Club   
106872  39.211160 -106.946080  Snowmass Ice Age Discovery Center   
65599   30.358280  -97.577210                        Manor Downs   
104303  39.883170  -84.286184                Englewood MetroPark   
54915   36.011747  -76.546138       Chowan Golf and Country Club   
65584   32.269470  -97.558118                Cleburne State Park   
56137   43.188476 -124.389793           Bandon Dunes Golf Resort   
32927   39.843217  -88.976850          Kirkland Fine Arts Center   
106871  39.213864 -106.936597         Anderson Ranch Arts Center   
106818  40.154486 -106.908700               Yampa Public Library   
32959   39.841090  -88.974570                Millikin University   
36048   33.711516 -116.183904                Spotlight 29 Casino   
106817  40.150218 -106.904639               Yampa Community Park   
34492   39.812204 -120.464206           Portola Visitor's Center   
70804   42.322280  -79.578103                          Westfield   
71275   42.322494  -79.577459                     McClurg Museum   
36464   33.740738 -116.185892            Golf Club at Terra Lago   
55618   34.060340  -95.382475               Hugo Lake State Park   
37162   39.190327 -106.881176   West Buttermilk Express Ski Lift   
34491   39.805206 -120.465370                  Portola City Park   
34350   39.305318 -120.333300                         Sugar Bowl   
36463   33.718905 -116.189910            Eagle Falls Golf Course   
106865  39.223709 -106.925930                      Snowmass Club   
34938   35.123445 -120.577094                    Swinging Bridge   
65480   30.352760  -97.557010               ShadowGlen Golf Club   
41956   39.038445  -80.471078              Weston State Hospital   
34490   39.805136 -120.473468    Western Pacific Railroad Museum   
106873  39.225503 -106.920617             Snowmass Rodeo Grounds   
109581  39.995166  -82.868565                Airport Golf Course   
35458   34.965479 -120.650262             Guadalupe-Nipomo Dunes   
34349   39.335614 -120.351056             Boreal Mountain Resort   
33091   55.449217 -129.457740                          Alice Arm   
106667  38.547240 -106.917690  Western State Colorado University   
106666  38.544380 -106.917620            Gunnison Pioneer Museum   
109353  39.843217  -88.976850          Kirkland Fine Arts Center   
109579  39.934993  -82.873821       Fort Rapids Indoor Waterpark   
65951   31.028978  -97.478882            Bell County Expo Center   
109363  39.841090  -88.974570                Millikin University   
111371  42.606100  -72.273033                        East Orange   
55552   35.667862  -99.801143   Black Kettle National Grasslands   
34941   35.062882 -120.623488       Pismo Dunes Natural Preserve   
65228   31.037889  -97.537392                    Stillhouse Park   

       Obj_AirportCodes        lat         lng  \
45482               ORD  41.978100  -87.906097   
92165               GUM  13.481700  144.793304   
45782               ORD  41.978100  -87.906097   
49144               MCI  39.292801  -94.726700   
109361              HSV  34.642799  -86.775597   
65949               HOU  29.645000  -95.278603   
34529               SFO  37.619400 -122.372803   
66086               HOU  29.645000  -95.278603   
65478               IAH  29.983299  -95.339996   
106872              COS  38.808899 -104.7

In [32]:
ca = result.loc[result['country_name'] == 'Canada']
fig = go.Figure(data=[go.Histogram(x=ca['distance_km'], histnorm='probability')])
fig.update_layout(title_text='POI and airport pairs distance probability distribution in Canada')
fig.show()

In [33]:
ca['distance_km'].describe()

count     5211.000000
mean       229.892908
std        803.737055
min          0.000000
25%         13.479291
50%         48.297635
75%        139.779425
max      15273.211925
Name: distance_km, dtype: float64

In [34]:
ca.sort_values(by=['distance_km'], ascending=False).head(50)

Obj_Lat     Obj_Lon                                   Obj_Name  \
53632 -25.274398  133.775136                           Sydney surrounds   
75635 -33.445061  149.554473                      Mount Panorama Winery   
75636 -33.439235  149.561857               National Motor Racing Museum   
75632 -33.417653  149.581031                                   Bathurst   
75634 -33.418171  149.586898        Bathurst Visitor Information Centre   
33904   0.000000    0.000000              Save on Foods Memorial Centre   
34002   0.000000    0.000000              Save on Foods Memorial Centre   
80689   0.000000    0.000000                  Bell MTS Place (Manitoba)   
56613 -76.016094  -30.234375                                  Tremblant   
55427  60.516009 -150.701988                              Bings Landing   
79729  45.245556  -66.090420                                  Doc Creek   
79736  45.245556  -66.090420                                  Doc Creek   
80984  45.662881  -75.346156                                       Mayo   
33837  46.214970  -63.491170                         Victoria Playhouse   
33973  46.214970  -63.491170                         Victoria Playhouse   
80284  49.102842 -118.677686                           Greenwood Museum   
79245  45.783333  -75.316667                              Knights Inlet   
79268  45.783333  -75.316667                              Knights Inlet   
79768  45.783333  -75.316667                              Knights Inlet   
79860  56.130366 -106.346771                            Daniels Harbour   
80248  56.130366 -106.346771                            Daniels Harbour   
81075  56.130366 -106.346771                                     Saglek   
33639  42.870723  -79.355188                                    Burnaby   
33647  43.647935  -79.381752                         Financial District   
56621  51.268700 -117.509167                      Glacier National Park   
57223  51.283040 -117.074430              Stairway to Heaven Chair Lift   
57222  51.298110 -117.054860                         Pioneer Chair Lift   
56950  51.299077 -117.052454              Kicking Horse Mountain Resort   
57221  51.297740 -117.048380                       Golden Eagle Express   
57220  51.297280 -117.047920                       Catamount Chair Lift   
57227  51.408800 -117.043170   Burges and James Gadsden Provincial Park   
57219  51.412520 -117.009800       Northern Lights Wildlife Wolf Center   
57218  51.332800 -117.007710                           Golden Golf Club   
57228  51.318700 -116.971980                          Edelweiss Village   
57226  51.299660 -116.968370            Kicking Horse Pedestrian Bridge   
57230  51.296520 -116.966700       Golden and District General Hospital   
57225  51.292190 -116.961450                 Golden and District Museum   
57229  51.296172 -116.955555       College of the Rockies Golden Campus   
57109  51.301920 -116.954290  British Columbia Visitor Centre at Golden   
57231  51.296194 -116.953213      Golden and District Recreation Centre   
56622  51.403868 -116.482024                         Yoho National Park   
80381  56.304670 -112.232341                                 Lagrande 4   
80752  56.130366 -106.346771                                     Saglek   
80073  45.984348  -73.446481                                    St Paul   
55733  50.302757 -119.213956                                Silver Star   
80888  56.130366 -106.346771                         Maricourt Airstrip   
80889  56.130366 -106.346771                                     Saglek   
80252  49.166706  -57.431632                                  Deer Lake   
79532  56.130366 -106.346771                         Maricourt Airstrip   
79900  45.984348  -73.446481                                    St Paul   

      Obj_AirportCodes        lat         lng                            name  \
53632              YQY  46.166698  -60.049999            J.A. Douglas McCurdy   
75635              ZB

In [35]:
ca.loc[ca['distance_km'] <= 250].sort_values(by=['distance_km'], ascending=False).head(50)

Obj_Lat     Obj_Lon  \
33319  50.446793 -116.249903   
57837  45.710360  -73.622144   
80417  50.327661  -64.037784   
33316  50.447290 -116.246240   
33315  50.456580 -116.241590   
79624  50.327661  -64.037784   
33313  50.458700 -116.239920   
33134  50.458341 -116.238962   
57899  45.481854  -73.599725   
33218  50.460552 -116.238275   
33314  50.456420 -116.238020   
57900  45.485121  -73.596354   
33317  50.445060 -116.232220   
57944  45.408900  -73.574640   
33318  50.428260 -116.215210   
33122  51.412435 -116.227387   
81088  55.230432  -85.127015   
57901  45.375508  -73.567058   
57211  46.663985  -71.572133   
57549  45.675976  -73.579375   
80405  54.993894  -85.427741   
80067  52.075279 -111.445261   
57626  46.201054  -73.584195   
79896  54.897412 -112.192975   
57200  45.636680  -75.938630   
57199  45.634848  -75.935829   
56768  48.555137  -71.768621   
56769  48.550990  -71.780904   
57198  45.645618  -75.919294   
57940  46.288730  -73.561360   
57597  46.289160  -73.560358   
33282  51.327887 -116.181668   
79270  50.683824 -127.377235   
56716  46.866475  -71.639686   
57580  45.528140  -73.513530   
56715  46.867539  -71.642030   
33175  51.441530 -116.162840   
79708  62.383899 -140.852917   
33216  51.440901 -116.162531   
33239  51.443148 -116.161194   
33235  51.442158 -116.161194   
33233  51.442881 -116.160979   
57582  45.542051  -73.510654   
55424  41.251581  -80.829609   
57073  45.639713  -75.885520   
57956  45.723948  -73.507869   
79687  55.134562 -121.012398   
33126  51.633432 -111.901806   
57584  45.536588  -73.491184   
33243  51.453071 -116.141195   

                                                Obj_Name Obj_AirportCodes  \
33319                               Greywolf Golf Course              YYC   
57837                                         Multiglace              YQB   
80417                                             Mingan              YZV   
33316                                 Sunbird Chair Lift              YYC   
33315                                    Toby Chair Lift              YYC   
79624                                             Mingan              YNA   
33313                                    Village Gondola              YYC   
33134                                           Panorama              YYC   
57899                         Westmount Park and Library              YQB   
33218                         Panorama Mountain Ski Area              YYC   
33314                                Mile 1 Quad Express              YYC   
57900                                Westmount City Hall              YQB   
33317                                  Champagne Express              YYC   
57944                                       Recre-O-Parc              YQB   
33318                                        Summit Quad              YYC   
33122                                        Lake Louise              YYC   
81088                                             Winisk              YWP   
57901                            Canadian Railway Museum              YQB   
57211                        Les Rendez-vous d'Autrefois              YUL   
57549                               Arena Saint-Francois              YQB   
80405                                          Peawanuck              YER   
80067                                         Coronation              YEG   
57626  Parc Regional des Chutes Monte-a-Peine-et-des-...              YQB   
79896                                          Lac Biche              YLL   
57200                                  Maclaren Cemetery              YUL   
57199                                      MacLaren Mill              YUL   
56768                              Lac St Jean Golf Club              YUL   
56769                                  Lac St Jean Beach              YUL   
57198                           Wakefield Covered Bridge              YUL   
57940                   Super Glissades St-Jean-de-Matha          